In [0]:
from pyspark.sql import functions as F
from pyspark.sql.types import ArrayType, StructType, StructField, StringType, IntegerType


In [0]:
# --- 1. SETUP PATHS ---
PATH_SCORES      = "/Volumes/workspace/default/rawdata/steam/combined_reviews.csv"
PATH_REVIEWS     = "/Volumes/workspace/default/rawdata/steam/processed/reviews.csv"
PATH_APPS_MAIN   = "/Volumes/workspace/default/rawdata/steam/applications.csv"
PATH_APPS_SHOTS  = "/Volumes/workspace/default/rawdata/steam/processed/appid and screenshots.csv"
PATH_OUTPUT_BASE = "/Volumes/workspace/default/rawdata/steam/processed/combined_reviews"


In [0]:
# 1. Load your uploaded CSV (combined_reviews.csv)
# (Make sure to upload the file to DBFS or use the correct path)
df_local = spark.read.csv("/Volumes/workspace/default/rawdata/steam/combined_reviews.csv", header=True, inferSchema=True)

# 2. Load the main Reviews table (the one that HAS the appid)
# Replace 'reviews' with your actual table name if it's different
df_main =  (
    spark.read
    .format("csv")
    .option("header", "true")
    .option("inferSchema", "true")
    .option("multiLine", "true")
    .option("quote", "\"")
    .option("escape", "\"")
    .option("mode", "PERMISSIVE")
    .option("encoding", "UTF-8")
    .load("/Volumes/workspace/default/rawdata/steam/processed/reviews.csv")
)

# 3. Join them on 'recommendationid' to get the 'app_id'
# Note: Check if your table uses 'app_id' or 'appid'. I use 'app_id' below.
df_joined = df_local.join(df_main, "recommendationid", "left") \
    .select(
        df_local["*"],                 # Keep your score/category
        df_main["appid"].alias("appid") # Add the App ID
    )

# 4. Save the result to a single CSV file
# We use coalesce(1) to force it into one file for easy download
output_path = "/Volumes/workspace/default/rawdata/steam/processed/combined_reviews_with_appid"
df_joined.coalesce(1).write.mode("overwrite").option("header", "true").csv(output_path)

print(f"✅ Success! File saved to: {output_path}")
print("Go to the DBFS File Browser, download the part-00000...csv file, rename it to 'combined_reviews_fixed.csv', and give it to the bot.")

✅ Success! File saved to: /Volumes/workspace/default/rawdata/steam/processed/combined_reviews_with_appid
Go to the DBFS File Browser, download the part-00000...csv file, rename it to 'combined_reviews_fixed.csv', and give it to the bot.


In [0]:
# --- 2. GET TARGET LIST (Games to process) ---
print("⏳ Building Target Game List...")
df_local = spark.read.csv(PATH_SCORES, header=True, inferSchema=False)
df_reviews = spark.read.option("header", "true").csv(PATH_REVIEWS)

# Filter IDs to be numbers only
df_local = df_local.filter(F.col("recommendationid").rlike("^[0-9]+$"))
df_reviews = df_reviews.filter(F.col("appid").rlike("^[0-9]+$"))

# Join to get the list of AppIDs
df_targets = df_local.join(df_reviews, "recommendationid", "left").select(
    df_reviews["appid"]
).distinct().filter(F.col("appid").isNotNull())


⏳ Building Target Game List...


In [0]:

# --- 3. GENERATE FILE 1: IMAGES (One row per app) ---
print("🖼️ Generating Images File (Header & Background)...")

df_apps_main = spark.read.option("header", "true").option("multiLine", "true").csv(PATH_APPS_MAIN)
# Clean column names
for c in df_apps_main.columns: df_apps_main = df_apps_main.withColumnRenamed(c, c.strip())

df_img_out = df_targets.join(df_apps_main, "appid", "inner").select(
    F.col("appid"),
    F.col("header_image"),
    F.col("background")
).distinct()

# Save
df_img_out.coalesce(1).write.mode("overwrite").option("header", "true").csv(f"{PATH_OUTPUT_BASE}_images")



🖼️ Generating Images File (Header & Background)...


In [0]:



# --- 4. GENERATE FILE 2: SCREENSHOTS (Multiple rows per app - URLs only) ---
print("📸 Generating Screenshots File (Extracted URLs)...")

df_shots_raw = spark.read.option("header", "true").option("multiLine", "true").option("escape", "\"").csv(PATH_APPS_SHOTS)
# Clean column names
for c in df_shots_raw.columns: df_shots_raw = df_shots_raw.withColumnRenamed(c, c.strip())

# Define Schema to parse the JSON string
# We only care about "path_full" inside the array of objects
json_schema = ArrayType(StructType([
    StructField("path_full", StringType())
]))

# 1. Join with targets
# 2. Parse the JSON string into an Array
# 3. Explode the Array (Create 1 row per screenshot)
# 4. Select the URL
df_shots_out = df_targets.join(df_shots_raw, "appid", "inner") \
    .withColumn("parsed_json", F.from_json(F.col("screenshots"), json_schema)) \
    .withColumn("exploded_shot", F.explode(F.col("parsed_json"))) \
    .select(
        F.col("appid"),
        F.col("exploded_shot.path_full").alias("screenshot_url")
    )

# Save
df_shots_out.coalesce(1).write.mode("overwrite").option("header", "true").csv(f"{PATH_OUTPUT_BASE}_screenshots")

print("✅ DONE! You have two files to download:")
print(f"1. {PATH_OUTPUT_BASE}_images (Headers/Backgrounds)")
print(f"2. {PATH_OUTPUT_BASE}_screenshots (Clean URLs)")

📸 Generating Screenshots File (Extracted URLs)...
✅ DONE! You have two files to download:
1. /Volumes/workspace/default/rawdata/steam/processed/combined_reviews_images (Headers/Backgrounds)
2. /Volumes/workspace/default/rawdata/steam/processed/combined_reviews_screenshots (Clean URLs)


In [0]:
df_shots_out.display(5)

appid screenshot_url 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_3dc92cc8c67e8b4448f08fde9e4c5af17f973228.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_241f698f4fa204cba7e05059cf2ee4551971b56a.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_19aceb99061e0a0c154451f577b844ae8b09c46d.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_0a3d3bbdfe14ed863471af4a888169593d311d8d.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_45540987c47e9573f5d76fb1c71618009e5ccdf7.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_5a9b4a6c0b58c3a25172e956b80a30bb5a83c212.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_deb02ca461700988e07d3dc1fb36af5e099f3689.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_192e34e85c8d86dfb7031b6a7d59c1d99b12f3ae.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_fe7329905a75ac14941c80b07f4a6d57242dbec6.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_80cf9f2313a34ea7616f2b91e0e896433fb6bf77.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_96baf6f24b4d75a35c9aaf8a03e7b36d88bbc6b0.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_9d799380d4708acf4928db6fe2dd7b69f0adbad6.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_5d132a9bd18c8747a8c42c3b86e866f74304ec35.1920x1080.jpg?t=1727276265 1706310 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1706310/ss_60093c7d47eebbc3f0761cc653db7e9b0401f6f2.1920x1080.jpg?t=1727276265 1710740 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1710740/ss_572ddf6241f4aeba8f62df343ffdf3d9174a657a.1920x1080.jpg?t=1753962939 1710740 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1710740/ss_ad592818677b6079bd540ee0dde980a5d741b121.1920x1080.jpg?t=1753962939 1710740 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1710740/ss_4ae4e50f99f844183e47aa7642094c8c696ff60e.1920x1080.jpg?t=1753962939 1710740 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1710740/ss_212e39d7a0e4298634c135957764761cde1e8b6d.1920x1080.jpg?t=1753962939 1710740 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1710740/ss_525447842e4a23f17e6cb19438802ec0e2b9d763.1920x1080.jpg?t=1753962939 1710740 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1710740/ss_5ae5f8cef19d29ba3989aa3a0e59f5a68c8dd305.1920x1080.jpg?t=1753962939 1710740 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1710740/ss_98b0eb934902b0985da36ac9bb97872ebed60184.1920x1080.jpg?t=1753962939 1710740 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1710740/ss_2a3c3381691395e94ae5ef066520de55950a0d63.1920x1080.jpg?t=1753962939 1710740 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1710740/ss_68b836658e512d84755b55cf8a7245156b1ed9ce.1920x1080.jpg?t=1753962939 1710740 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1710740/ss_f6b68547653d111ea75f94dfe5167a78fcc9b16d.1920x1080.jpg?t=1753962939 1710740 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1710740/ss_9c88c766d07888bd14d3d0daf5c6434fb72bc3ac.1920x1080.jpg?t=1753962939 1710740 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/1710740/ss_95445e4bc819cd7cddf7a1380600b22b347d8259.19

In [0]:
df_img_out.display(5)

appid header_image background 3322 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/3322/header.jpg?t=1447350891 https://store.akamai.steamstatic.com/images/storepagebackground/app/3322?t=1447350891 17520 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/17520/header.jpg?t=1734564871 https://store.akamai.steamstatic.com/images/storepagebackground/app/17520?t=1734564871 99410 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/99410/header.jpg?t=1663910191 https://store.akamai.steamstatic.com/images/storepagebackground/app/99410?t=1663910191 241300 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/241300/header.jpg?t=1632146375 https://store.akamai.steamstatic.com/images/storepagebackground/app/241300?t=1632146375 257120 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/257120/header.jpg?t=1725546457 https://store.akamai.steamstatic.com/images/storepagebackground/app/257120?t=1725546457 257350 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/257350/header.jpg?t=1746199025 https://store.akamai.steamstatic.com/images/storepagebackground/app/257350?t=1746199025 299780 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/299780/header.jpg?t=1665608332 https://store.akamai.steamstatic.com/images/storepagebackground/app/299780?t=1665608332 370150 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/370150/header.jpg?t=1696352458 https://store.akamai.steamstatic.com/images/storepagebackground/app/370150?t=1696352458 379575 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/379575/header.jpg?t=1537258544 https://store.akamai.steamstatic.com/images/storepagebackground/app/379575?t=1537258544 455400 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/455400/header.jpg?t=1580375468 https://store.akamai.steamstatic.com/images/storepagebackground/app/455400?t=1580375468 478042 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/478042/header.jpg?t=1530523341 https://store.akamai.steamstatic.com/images/storepagebackground/app/478042?t=1530523341 509340 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/509340/header.jpg?t=1470361615 https://store.akamai.steamstatic.com/images/storepagebackground/app/509340?t=1470361615 510990 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/510990/header.jpg?t=1483948525 https://store.akamai.steamstatic.com/images/storepagebackground/app/510990?t=1483948525 541830 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/541830/header.jpg?t=1476802129 https://store.akamai.steamstatic.com/images/storepagebackground/app/541830?t=1476802129 543220 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/543220/header.jpg?t=1484598675 https://store.akamai.steamstatic.com/images/storepagebackground/app/543220?t=1484598675 555830 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/555830/header.jpg?t=1560499109 https://store.akamai.steamstatic.com/images/storepagebackground/app/555830?t=1560499109 558762 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/558762/header.jpg?t=1669019635 https://store.akamai.steamstatic.com/images/storepagebackground/app/558762?t=1669019635 645940 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/645940/header.jpg?t=1509211511 https://store.akamai.steamstatic.com/images/storepagebackground/app/645940?t=1509211511 690400 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/690400/header.jpg?t=1508410960 https://store.akamai.steamstatic.com/images/storepagebackground/app/690400?t=1508410960 717060 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/717060/header.jpg?t=1508442208 https://store.akamai.steamstatic.com/images/storepagebackground/app/717060?t=1508442208 720780 https://shared.akamai.steamstatic.com/store_item_assets/steam/apps/720780/header.jpg?t=1633010501 https://store.aka

In [0]:
# --- MERGE SCORES + IMAGES INTO ONE MASTER FILE ---
print("🖼️ Generating Master File (Scores + AppID + Images)...")

# 1. Prepare the Applications Data
df_apps_main = spark.read.option("header", "true").option("multiLine", "true").csv(PATH_APPS_MAIN)
for c in df_apps_main.columns: df_apps_main = df_apps_main.withColumnRenamed(c, c.strip())

# 2. Re-create the joined reviews (Scores + AppID)
# We join 'df_local' (your scores) with 'df_reviews' (the bridge)
df_joined_scores = df_local.join(df_reviews, "recommendationid", "left").select(
    df_local["*"],
    df_reviews["appid"]
).filter(F.col("appid").isNotNull())

# 3. Join Scores with Images
# We use a LEFT join so we don't lose any review scores even if the game is missing an image
df_master = df_joined_scores.join(df_apps_main, "appid", "left").select(
    df_joined_scores["*"],
    df_apps_main["header_image"],
    df_apps_main["background"]
)

# 4. Save
path_master = f"{PATH_OUTPUT_BASE}_master"
df_master.coalesce(1).write.mode("overwrite").option("header", "true").csv(path_master)

print(f"✅ Master File Saved: {path_master}")
print("   (This file contains Scores, AppIDs, and Images all in one)")

🖼️ Generating Master File (Scores + AppID + Images)...
✅ Master File Saved: /Volumes/workspace/default/rawdata/steam/processed/combined_reviews_master
   (This file contains Scores, AppIDs, and Images all in one)


In [0]:
# --- CLEANUP: REMOVE _c0 COLUMN ---
PATH_MASTER = "/Volumes/workspace/default/rawdata/steam/processed/combined_reviews_master"

print(f"🧹 Cleaning file at: {PATH_MASTER} ...")

# 1. Read the file
df_master = spark.read.option("header", "true").option("multiLine", "true").csv(PATH_MASTER)

# 2. Drop the unwanted column
if "_c0" in df_master.columns:
    df_clean = df_master.drop("_c0", "category")
    print("   ✅ Found and dropped '_c0' column.")
else:
    df_clean = df_master
    print("   ℹ️ '_c0' column not found (already clean).")

# 3. Overwrite the file with the clean version
df_clean.coalesce(1).write.mode("overwrite").option("header", "true").csv(PATH_MASTER)

print("✅ Cleanup Done! You can now download the clean file.")

🧹 Cleaning file at: /Volumes/workspace/default/rawdata/steam/processed/combined_reviews_master ...
   ✅ Found and dropped '_c0' column.
✅ Cleanup Done! You can now download the clean file.
